# Model simulation without RL

In [88]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from IPython.display import HTML
import torch
import torch.nn as nn
import torch.optim as optim
from matplotlib.lines import Line2D

# Set random seed for reproducibility
seed = 42
np.random.seed(seed)

# Set global constants
DT = 0.3

In [89]:
class ReplayBuffer:
    def __init__(self, capacity=10000):
        self.buffer = []
        self.capacity = capacity

    def add(self, experience):
        if len(self.buffer) >= self.capacity:
            self.buffer.pop(0)
        self.buffer.append(experience)

    def sample(self, batch_size):
        return np.random.sample(self.buffer, batch_size)

In [90]:
class ActorNetwork(nn.Module):
    def __init__(self, input_dim, output_dim):
        super(ActorNetwork, self).__init__()
        self.fc1 = nn.Linear(input_dim, 128)
        self.fc2 = nn.Linear(128, 128)
        self.fc3 = nn.Linear(128, output_dim)

    def forward(self, x):
        x = torch.relu(self.fc1(x))
        x = torch.relu(self.fc2(x))
        x = torch.tanh(self.fc3(x))  # Actions are continuous, scaled between -1 and 1
        return x

In [91]:
class CriticNetwork(nn.Module):
    def __init__(self, input_dim):
        super(CriticNetwork, self).__init__()
        self.fc1 = nn.Linear(input_dim, 128)
        self.fc2 = nn.Linear(128, 128)
        self.fc3 = nn.Linear(128, 1)

    def forward(self, x):
        x = torch.relu(self.fc1(x))
        x = torch.relu(self.fc2(x))
        x = self.fc3(x)
        return x

more accurate (passive forces + 6 nearest prey n predator)

In [92]:
class Agent:
    def __init__(self, position, speed, mass, max_acceleration, max_angular_velocity, agent_type):
        # Set up initial position
        self.position = np.array(position, dtype=float)

        # Set up initial velocity vector with magnitude speed
        self.velocity = np.random.uniform(-1, 1, 2)
        if np.linalg.norm(self.velocity) == 0:
            self.velocity = np.array([1.0, 0.0])
        else:
            self.velocity = (self.velocity / np.linalg.norm(self.velocity)) * speed

        self.mass = 1.0  # as per article
        self.type = agent_type

        # Calculate heading angle and heading vector based on initial velocity
        self.heading_angle = np.arctan2(self.velocity[1], self.velocity[0])
        self.heading_vector = np.array([np.cos(self.heading_angle), np.sin(self.heading_angle)])

        self.acceleration = np.zeros(2)
        self.max_acceleration = max_acceleration
        self.max_angular_velocity = max_angular_velocity
        self.position_history = [self.position.copy()]
        self.collision_force = np.zeros(2)

        # Agent parameters
        self.drag_coefficient = 0.2
        self.stiffness_coefficient = 5.0
        self.radius = 2.0 if agent_type == 'predator' else 1.0

    def move(self, dt=DT):
        pass

    def apply_boundary_conditions(self, width, height):
        self.position = self.position % np.array([width, height])

    def get_observation(self):
        # Same topological limit as implemented previously:
        # Keep the nearest 6 allies and 6 adversaries
        R = max(env.width, env.height)
        allies = []
        adversaries = []
        for other in env.agents:
            if other is self:
                continue
            distance_vector = other.position - self.position
            distance_vector = env.apply_periodic_adjustment(distance_vector)
            dist = np.linalg.norm(distance_vector)
            if dist <= R:
                if other.type == self.type:
                    allies.append((dist, other))
                else:
                    adversaries.append((dist, other))

        allies.sort(key=lambda x: x[0])
        adversaries.sort(key=lambda x: x[0])
        allies = allies[:6]
        adversaries = adversaries[:6]

        obs_allies = []
        for _, ally in allies:
            dist_vec = ally.position - self.position
            dist_vec = env.apply_periodic_adjustment(dist_vec)
            rel_heading = ally.heading_vector - self.heading_vector
            obs_allies.extend([dist_vec[0], dist_vec[1], rel_heading[0], rel_heading[1]])

        while len(obs_allies) < 24:  # 6 allies * 4 values each =24
            obs_allies.extend([0,0,0,0])

        obs_adversaries = []
        for _, adv in adversaries:
            dist_vec = adv.position - self.position
            dist_vec = env.apply_periodic_adjustment(dist_vec)
            rel_heading = adv.heading_vector - self.heading_vector
            obs_adversaries.extend([dist_vec[0], dist_vec[1], rel_heading[0], rel_heading[1]])

        while len(obs_adversaries) < 24: # 6 adv *4=24
            obs_adversaries.extend([0,0,0,0])

        self_state = np.concatenate([self.position, self.velocity, self.heading_vector])
        observation = np.concatenate([obs_allies, obs_adversaries, self_state])
        return observation

In [93]:
class Prey(Agent):
    def __init__(self, position, **kwargs):
        super().__init__(position, speed=1.0, mass=1.0, max_acceleration=1.0, max_angular_velocity=1.0, agent_type='prey')
        self.is_captured = False

    def move(self, dt=DT):
        # Instead of random large turns, let's simplify to a small random action or zero:
        # In the article, actions come from RL. For now, we can set small random actions:
        aF = np.random.uniform(0, self.max_acceleration)
        aR = np.random.uniform(-self.max_angular_velocity, self.max_angular_velocity)

        # Update heading angle
        self.heading_angle += aR * dt
        self.heading_vector = np.array([np.cos(self.heading_angle), np.sin(self.heading_angle)])

        propulsion_force = aF * self.heading_vector
        drag_force = -self.drag_coefficient * self.velocity
        collision_force = self.collision_force
        total_force = propulsion_force + drag_force + collision_force

        prev_speed = np.linalg.norm(self.velocity)
        self.velocity += (total_force / self.mass) * dt
        new_speed = np.linalg.norm(self.velocity)

        # Update position
        self.position += self.velocity * dt
        self.apply_boundary_conditions(env.width, env.height)
        self.collision_force = np.zeros(2)

        self.position_history.append(self.position.copy())
        if len(self.position_history) > 10:
            self.position_history.pop(0)

        # Check if caught
        self.is_captured = False
        for agent in env.agents:
            if agent.type == 'predator':
                dist_vec = agent.position - self.position
                dist_vec = env.apply_periodic_adjustment(dist_vec)
                dist = np.linalg.norm(dist_vec)
                if dist < (self.radius + agent.radius):
                    self.is_captured = True
                    break

        # Rewards as per the article:
        # Prey: -1 if caught, else 0
        # plus decorative cost: -0.01|aF| -0.1|aR|
        reward = -1.0 if self.is_captured else 0.0
        reward += (-0.01*abs(aF) - 0.1*abs(aR))

        observation = self.get_observation()
        state = observation
        action = np.array([aF, aR])
        next_state = self.get_observation()
        env.replay_buffer_prey.add((state, action, reward, next_state))

In [94]:
class Predator(Agent):
    def __init__(self, position, **kwargs):
        super().__init__(position, speed=2, mass=1.0, max_acceleration=1.5, max_angular_velocity=1, agent_type='predator')

    def move(self, dt=DT):
        # Simple random actions for demonstration:
        aF = np.random.uniform(0, self.max_acceleration)
        aR = np.random.uniform(-self.max_angular_velocity, self.max_angular_velocity)

        self.heading_angle += aR * dt
        self.heading_vector = np.array([np.cos(self.heading_angle), np.sin(self.heading_angle)])

        propulsion_force = aF * self.heading_vector
        drag_force = -self.drag_coefficient * self.velocity
        collision_force = self.collision_force
        total_force = propulsion_force + drag_force + collision_force

        prev_speed = np.linalg.norm(self.velocity)
        self.velocity += (total_force / self.mass) * dt
        new_speed = np.linalg.norm(self.velocity)

        self.position += self.velocity * dt
        self.apply_boundary_conditions(env.width, env.height)
        self.collision_force = np.zeros(2)

        self.position_history.append(self.position.copy())
        if len(self.position_history) > 10:
            self.position_history.pop(0)

        # Check if caught prey
        captured_prey = False
        for agent in env.agents:
            if agent.type == 'prey':
                dist_vec = agent.position - self.position
                dist_vec = env.apply_periodic_adjustment(dist_vec)
                dist = np.linalg.norm(dist_vec)
                if dist < (self.radius + agent.radius):
                    captured_prey = True
                    break

        # Predator reward from article:
        # Predator: +1 if capturing prey, else 0
        # minus decorative cost: -0.01|aF| -0.1|aR|
        reward = 1.0 if captured_prey else 0.0
        reward += (-0.01*abs(aF) - 0.1*abs(aR))

        observation = self.get_observation()
        state = observation
        action = np.array([aF, aR])
        next_state = self.get_observation()
        env.replay_buffer_predator.add((state, action, reward, next_state))

In [95]:
class PredatorPreyEnvironment:
    def __init__(self, width=100, height=100):
        self.width = width
        self.height = height
        self.agents = []
        self.replay_buffer_prey = ReplayBuffer(capacity=10000)
        self.replay_buffer_predator = ReplayBuffer(capacity=10000)

    def add_agent(self, agent):
        self.agents.append(agent)

    def update(self, dt=0.3):
        self.compute_collision_forces()
        for agent in self.agents[:]:
            agent.move(dt=dt)

    def compute_collision_forces(self):
        for agent in self.agents:
            agent.collision_force = np.zeros(2)

        num_agents = len(self.agents)
        for i in range(num_agents):
            agent_i = self.agents[i]
            for j in range(i + 1, num_agents):
                agent_j = self.agents[j]
                distance_vector = agent_i.position - agent_j.position
                distance_vector = self.apply_periodic_adjustment(distance_vector)
                distance = np.linalg.norm(distance_vector)
                min_distance = agent_i.radius + agent_j.radius
                if distance < min_distance and distance > 0:
                    overlap = min_distance - distance
                    direction = distance_vector / distance
                    
                    agent_i.collision_force += agent_i.stiffness_coefficient * overlap * direction
                    agent_j.collision_force -= agent_j.stiffness_coefficient * overlap * direction

    def apply_periodic_adjustment(self, vector):
        adjusted_vector = vector.copy()
        if vector[0] > self.width / 2:
            adjusted_vector[0] -= self.width
        elif vector[0] < -self.width / 2:
            adjusted_vector[0] += self.width
        if vector[1] > self.height / 2:
            adjusted_vector[1] -= self.height
        elif vector[1] < -self.height / 2:
            adjusted_vector[1] += self.height
        return adjusted_vector

    def find_nearest_prey(self, predator):
        nearest_prey = None
        min_distance = float('inf')
        for agent in self.agents:
            if agent.type == 'prey':
                distance_vector = agent.position - predator.position
                distance_vector = self.apply_periodic_adjustment(distance_vector)
                distance = np.linalg.norm(distance_vector)
                if distance < min_distance:
                    min_distance = distance
                    nearest_prey = agent
        return nearest_prey

    def find_nearest_predator(self, prey, perception_range=30.0):
        nearest_predator = None
        min_distance = float('inf')
        for agent in self.agents:
            if agent.type == 'predator':
                distance_vector = agent.position - prey.position
                distance_vector = self.apply_periodic_adjustment(distance_vector)
                distance = np.linalg.norm(distance_vector)
                if distance < min_distance and distance <= perception_range:
                    min_distance = distance
                    nearest_predator = agent
        return nearest_predator

    def adjust_positions_for_traces(self, positions):
        adjusted_positions = [positions[0]]
        for i in range(1, len(positions)):
            prev = adjusted_positions[-1]
            curr = positions[i].copy()
            dx = curr[0] - prev[0]
            dy = curr[1] - prev[1]

            if dx > self.width / 2:
                curr[0] -= self.width
            elif dx < -self.width / 2:
                curr[0] += self.width

            if dy > self.height / 2:
                curr[1] -= self.height
            elif dy < -self.height / 2:
                curr[1] += self.height

            adjusted_positions.append(curr)
        return np.array(adjusted_positions)

    def get_agent_shape(self, agent):
        direction = agent.heading_vector
        direction = direction / np.linalg.norm(direction)
        perp_direction = np.array([-direction[1], direction[0]])
        size = agent.radius * 2
        front = agent.position + direction * size
        left = agent.position - direction * size * 0.5 + perp_direction * size * 0.5
        right = agent.position - direction * size * 0.5 - perp_direction * size * 0.5
        return [front, left, right]

    def animate(self, steps=100):
        fig, ax = plt.subplots(figsize=(5, 5))
        ax.set_xlim(0, self.width)
        ax.set_ylim(0, self.height)
        ax.set_xticks([])
        ax.set_yticks([])

        agent_artists = {}

        for agent in self.agents:
            if agent.type == 'prey':
                triangle = plt.Polygon(self.get_agent_shape(agent), closed=True, color='b')
                line, = ax.plot([], [], color='b', alpha=0.2)
            elif agent.type == 'predator':
                triangle = plt.Polygon(self.get_agent_shape(agent), closed=True, color='orange', alpha=0.8)
                line, = ax.plot([], [], color='orange', alpha=0.2)
            agent_artists[agent] = {'patch': triangle, 'trace': line}
            ax.add_patch(triangle)

        def update(frame):
            self.update(dt=0.3)
            for agent in self.agents:
                artist = agent_artists.get(agent)
                if artist:
                    patch = artist['patch']
                    trace = artist['trace']
                    patch.set_xy(self.get_agent_shape(agent))
                    positions = np.array(agent.position_history)
                    positions = self.adjust_positions_for_traces(positions)
                    trace.set_data(positions[:, 0], positions[:, 1])
                else:
                    # If new agents were added, handle here
                    pass

            # Remove agents not in environment
            agents_to_remove = [a for a in agent_artists if a not in self.agents]
            for a in agents_to_remove:
                aa = agent_artists.pop(a)
                aa['patch'].remove()
                aa['trace'].remove()

            return []

        # Change repeat to True to loop animation
        ani = animation.FuncAnimation(fig, update, frames=steps, blit=False, interval=50, repeat=True)
        plt.close(fig)
        return HTML(ani.to_jshtml())


In [96]:
# Create environment instance
width = 70
env = PredatorPreyEnvironment(width, width)

# Add prey agents
num_prey = 15
for _ in range(num_prey):
    initial_position = np.random.uniform(0, width, 2)
    prey = Prey(position=initial_position)
    env.add_agent(prey)

# Add predator agents
num_predators = 3
for _ in range(num_predators):
    initial_position = np.random.uniform(0, width, 2)
    predator = Predator(position=initial_position)
    env.add_agent(predator)

# Animate the environment
animation_html = env.animate(steps=200)
animation_html
